# Optional Lab: Gradient Descent for Logistic Regression

## Goals
In this lab, you will:
- update gradient descent for logistic regression.
- explore gradient descent on a familiar data set

In [1]:
import copy, math
import numpy as np
%matplotlib widget
import matplotlib.pyplot as plt
from lab_utils_common import  dlc, plot_data, plt_tumor_data, sigmoid, compute_cost_logistic
from plt_quad_logistic import plt_quad_logistic, plt_prob
plt.style.use('./deeplearning.mplstyle')

## Data set 
Let's start with the same two feature data set used in the decision boundary lab.

In [2]:
X_train = np.array([[0.5, 1.5], [1,1], [1.5, 0.5], [3, 0.5], [2, 2], [1, 2.5]])
y_train = np.array([0, 0, 0, 1, 1, 1])

As before, we'll use a helper function to plot this data. The data points with label $y=1$ are shown as red crosses, while the data points with label $y=0$ are shown as blue circles.

In [3]:
fig,ax = plt.subplots(1,1,figsize=(4,4))
plot_data(X_train, y_train, ax)

ax.axis([0, 4, 0, 3.5])
ax.set_ylabel('$x_1$', fontsize=12)
ax.set_xlabel('$x_0$', fontsize=12)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

## Logistic Gradient Descent
<img align="right" src="./images/C1_W3_Logistic_gradient_descent.png"     style=" width:400px; padding: 10px; " >

Recall the gradient descent algorithm utilizes the gradient calculation:
$$\begin{align*}
&\text{repeat until convergence:} \; \lbrace \\
&  \; \; \;w_j = w_j -  \alpha \frac{\partial J(\mathbf{w},b)}{\partial w_j} \tag{1}  \; & \text{for j := 0..n-1} \\ 
&  \; \; \;  \; \;b = b -  \alpha \frac{\partial J(\mathbf{w},b)}{\partial b} \\
&\rbrace
\end{align*}$$

Where each iteration performs simultaneous updates on $w_j$ for all $j$, where
$$\begin{align*}
\frac{\partial J(\mathbf{w},b)}{\partial w_j}  &= \frac{1}{m} \sum\limits_{i = 0}^{m-1} (f_{\mathbf{w},b}(\mathbf{x}^{(i)}) - y^{(i)})x_{j}^{(i)} \tag{2} \\
\frac{\partial J(\mathbf{w},b)}{\partial b}  &= \frac{1}{m} \sum\limits_{i = 0}^{m-1} (f_{\mathbf{w},b}(\mathbf{x}^{(i)}) - y^{(i)}) \tag{3} 
\end{align*}$$

* m is the number of training examples in the data set      
* $f_{\mathbf{w},b}(x^{(i)})$ is the model's prediction, while $y^{(i)}$ is the target
* For a logistic regression model  
    $z = \mathbf{w} \cdot \mathbf{x} + b$  
    $f_{\mathbf{w},b}(x) = g(z)$  
    where $g(z)$ is the sigmoid function:  
    $g(z) = \frac{1}{1+e^{-z}}$   
    


### Gradient Descent Implementation
The gradient descent algorithm implementation has two components: 
- The loop implementing equation (1) above. This is `gradient_descent` below and is generally provided to you in optional and practice labs.
- The calculation of the current gradient, equations (2,3) above. This is `compute_gradient_logistic` below. You will be asked to implement this week's practice lab.

#### Calculating the Gradient, Code Description
Implements equation (2),(3) above for all $w_j$ and $b$.
There are many ways to implement this. Outlined below is this:
- initialize variables to accumulate `dj_dw` and `dj_db`
- for each example
    - calculate the error for that example $g(\mathbf{w} \cdot \mathbf{x}^{(i)} + b) - \mathbf{y}^{(i)}$
    - for each input value $x_{j}^{(i)}$ in this example,  
        - multiply the error by the input  $x_{j}^{(i)}$, and add to the corresponding element of `dj_dw`. (equation 2 above)
    - add the error to `dj_db` (equation 3 above)

- divide `dj_db` and `dj_dw` by total number of examples (m)
- note that $\mathbf{x}^{(i)}$ in numpy `X[i,:]` or `X[i]`  and $x_{j}^{(i)}$ is `X[i,j]`

In [6]:
def compute_gradient_logistic(X, y, w, b): 
    """
    Computes the gradient for logistic regression 
 
    Args:
      X (ndarray (m,n): Data, m examples with n features
      y (ndarray (m,)): target values
      w (ndarray (n,)): model parameters  
      b (scalar)      : model parameter
    Returns
      dj_dw (ndarray (n,)): The gradient of the cost w.r.t. the parameters w. 
      dj_db (scalar)      : The gradient of the cost w.r.t. the parameter b. 
    """
    m,n = X.shape
    dj_dw = np.zeros((n,))                           #(n,)
    dj_db = 0.

    for i in range(m):
        f_wb_i = sigmoid(np.dot(X[i],w) + b)          #(n,)(n,)=scalar
        err_i  = f_wb_i  - y[i]                       #scalar
        for j in range(n):
            dj_dw[j] = dj_dw[j] + err_i * X[i,j]      #scalar
            print(dj_dw[j])
        
        print(dj_dw)
        dj_db = dj_db + err_i
    dj_dw = dj_dw/m                                   #(n,)
    dj_db = dj_db/m                                   #scalar
        
    return dj_db, dj_dw  

Check the implementation of the gradient function using the cell below.

In [7]:
X_tmp = np.array([[0.5, 1.5], [1,1], [1.5, 0.5], [3, 0.5], [2, 2], [1, 2.5]])
y_tmp = np.array([0, 0, 0, 1, 1, 1])
w_tmp = np.array([2.,3.])
b_tmp = 1.
dj_db_tmp, dj_dw_tmp = compute_gradient_logistic(X_tmp, y_tmp, w_tmp, b_tmp)
print(f"dj_db: {dj_db_tmp}" )
print(f"dj_dw: {dj_dw_tmp.tolist()}" )

0.4992494088716315
1.4977482266148945
[0.5 1.5]
1.4967767857149967
2.4952756034582597
[1.5 2.5]
2.9906715791411527
2.9932405346003117
[2.99 2.99]
2.990061298206987
2.993138821111284
[2.99 2.99]
2.990027895363291
2.993105418267588
[2.99 2.99]
2.9900003596721763
2.9930365790398015
[2.99 2.99]
dj_db: 0.49861806546328574
dj_dw: [0.498333393278696, 0.49883942983996693]


In [11]:
def comp_grad_log(X, y, w, b):
    m = X.shape[0]
    f_wb = sigmoid(np.dot(X, w) + b)
    err = f_wb - y
    dj_dw = np.dot(X.T, err) / m
    dj_db = np.sum(err) / m
    
    return dj_dw, dj_db

X_tmp = np.array([[0.5, 1.5], [1,1], [1.5, 0.5], [3, 0.5], [2, 2], [1, 2.5]])
y_tmp = np.array([0, 0, 0, 1, 1, 1])
w_tmp = np.array([2.,3.])
b_tmp = 1.
dj_dw_tmp, dj_db_tmp = comp_grad_log(X_tmp, y_tmp, w_tmp, b_tmp)
print(f"dj_db: {dj_db_tmp}" )
print(f"dj_dw: {dj_dw_tmp.tolist()}" )

dj_db: 0.49861806546328574
dj_dw: [0.498333393278696, 0.49883942983996693]


**Expected output**
``` 
dj_db: 0.49861806546328574
dj_dw: [0.498333393278696, 0.49883942983996693]
```

#### Gradient Descent Code 
The code implementing equation (1) above is implemented below. Take a moment to locate and compare the functions in the routine to the equations above.

In [12]:
def gradient_descent(X, y, w_in, b_in, alpha, num_iters): 
    """
    Performs batch gradient descent
    
    Args:
      X (ndarray (m,n)   : Data, m examples with n features
      y (ndarray (m,))   : target values
      w_in (ndarray (n,)): Initial values of model parameters  
      b_in (scalar)      : Initial values of model parameter
      alpha (float)      : Learning rate
      num_iters (scalar) : number of iterations to run gradient descent
      
    Returns:
      w (ndarray (n,))   : Updated values of parameters
      b (scalar)         : Updated value of parameter 
    """
    # An array to store cost J and w's at each iteration primarily for graphing later
    J_history = []
    w = copy.deepcopy(w_in)  #avoid modifying global w within function
    b = b_in
    
    for i in range(num_iters):
        # Calculate the gradient and update the parameters
        dj_db, dj_dw = compute_gradient_logistic(X, y, w, b)   

        # Update Parameters using w, b, alpha and gradient
        w = w - alpha * dj_dw               
        b = b - alpha * dj_db               
      
        # Save cost J at each iteration
        if i<100000:      # prevent resource exhaustion 
            J_history.append( compute_cost_logistic(X, y, w, b) )

        # Print cost every at intervals 10 times or as many iterations if < 10
        if i% math.ceil(num_iters / 10) == 0:
            print(f"Iteration {i:4d}: Cost {J_history[-1]}   ")
        
    return w, b, J_history         #return final w,b and J history for graphing


Let's run gradient descent on our data set.

In [13]:
w_tmp  = np.zeros_like(X_train[0])
b_tmp  = 0.
alph = 0.1
iters = 10000

w_out, b_out, _ = gradient_descent(X_train, y_train, w_tmp, b_tmp, alph, iters) 
print(f"\nupdated parameters: w:{w_out}, b:{b_out}")

0.25
0.75
[0.25 0.75]
0.75
1.25
[0.75 1.25]
1.5
1.5
[1.5 1.5]
0.0
1.25
[0.   1.25]
-1.0
0.25
[-1.    0.25]
-1.5
-1.0
[-1.5 -1. ]
Iteration    0: Cost 0.684610468560574   
0.25468695076083037
0.7640608522824911
[0.25 0.76]
0.7651021106481951
1.2744760121698557
[0.77 1.27]
1.5322866024729722
1.530204176111448
[1.53 1.53]
0.09475045859120113
1.2906148187978195
[0.09 1.29]
-0.8636069706633129
0.3322573895433054
[-0.86  0.33]
-1.3469464740939014
-0.8760913690331662
[-1.35 -0.88]
0.25863835513327454
0.7759150653998237
[0.26 0.78]
0.7779349719702646
1.2952116822368138
[0.78 1.3 ]
1.5599088111999406
1.5558696286467057
[1.56 1.56]
0.17703659036613928
1.3253909251744056
[0.18 1.33]
-0.7451499740828886
0.4032043607253777
[-0.75  0.4 ]
-1.2141579795643684
-0.7693156529783216
[-1.21 -0.77]
0.2619539683365809
0.7858619050097427
[0.26 0.79]
0.7888036674912591
1.312711604164421
[0.79 1.31]
1.583488065376138
1.5776064034593806
[1.58 1.58]
0.24843876892758954
1.3550981873846226
[0.25 1.36]
-0.6423597385

0.2655700521131233
0.7967101563393699
[0.27 0.8 ]
0.8170324370741835
1.3481725413004302
[0.82 1.35]
1.674453821855688
1.6339796695609317
[1.67 1.63]
0.743229670232392
1.4787756442903823
[0.74 1.48]
0.08957004445559291
0.8251160185135833
[0.09 0.83]
-0.2948627006626514
-0.13596584428202751
[-0.29 -0.14]
0.2649864775500516
0.7949594326501548
[0.26 0.79]
0.8156171331631517
1.3455900882632548
[0.82 1.35]
1.672289903424238
1.6311476783502836
[1.67 1.63]
0.7444874282097679
1.4765139324812053
[0.74 1.48]
0.09250692935488558
0.824533433626323
[0.09 0.82]
-0.291917015893565
-0.13652642949480343
[-0.29 -0.14]
0.26440248377276676
0.7932074513183003
[0.26 0.79]
0.8141933874227533
1.342998354968287
[0.81 1.34]
1.6700950959828957
1.6282989244883344
[1.67 1.63]
0.7456215571842094
1.47422000135522
[0.75 1.47]
0.09528678760387954
0.8238852317748901
[0.1  0.82]
-0.2891324406466118
-0.13716283885133818
[-0.29 -0.14]
0.26381863731212396
0.7914559119363719
[0.26 0.79]
0.8127630525814553
1.3404003272057032


0.24893822902242896
0.7468146870672869
[0.25 0.75]
0.7745908720189674
1.2724673300638254
[0.77 1.27]
1.6044973431279614
1.54910282043349
[1.6  1.55]
0.7510507177525163
1.4068617162042492
[0.75 1.41]
0.14160063868792716
0.79741163713966
[0.14 0.8 ]
-0.24122879354988247
-0.15966194345486406
[-0.24 -0.16]
0.24842854314915652
0.7452856294474696
[0.25 0.75]
0.773233879671164
1.270090965969477
[0.77 1.27]
1.6021324680691484
1.546390495435472
[1.6  1.55]
0.7507072367580838
1.404486290216961
[0.75 1.4 ]
0.14264765696860304
0.7964267104274803
[0.14 0.8 ]
-0.24004151779131588
-0.16029622647231712
[-0.24 -0.16]
0.24792175989273774
0.7437652796782133
[0.25 0.74]
0.7718816271324596
1.2677251469179351
[0.77 1.27]
1.5997693583841468
1.543687724001831
[1.6  1.54]
0.7503401449192659
1.4021161884243507
[0.75 1.4 ]
0.1436687357834665
0.7954447792885513
[0.14 0.8 ]
-0.23887458044020815
-0.16091351127063536
[-0.24 -0.16]
0.24741784782037077
0.7422535434611123
[0.25 0.74]
0.7705340958546991
1.26536979149544

[0.73 1.2 ]
1.5323101210120222
1.4691831894800211
[1.53 1.47]
0.731905259898218
1.335782379294387
[0.73 1.34]
0.16448903567244477
0.7683661550686138
[0.16 0.77]
-0.21182501919818442
-0.17241898210795914
[-0.21 -0.17]
0.23390809061352547
0.7017242718405764
[0.23 0.7 ]
0.7333673102840736
1.2011834915111246
[0.73 1.2 ]
1.5300271960349214
1.4667367867614072
[1.53 1.47]
0.7310667507019449
1.3335767125392444
[0.73 1.33]
0.16496757165082843
0.7674775334881279
[0.16 0.77]
-0.2110768116479843
-0.17263342475890397
[-0.21 -0.17]
0.23347560700160544
0.7004268210048163
[0.23 0.7 ]
0.7321462561197177
1.1990974701229287
[0.73 1.2 ]
1.5277474378777143
1.4642978640422608
[1.53 1.46]
0.7302182083480755
1.331376325787321
[0.73 1.33]
0.1654334625081375
0.766591579947383
[0.17 0.77]
-0.21033842170740125
-0.1728381305914639
[-0.21 -0.17]
0.23304506920646834
0.6991352076194051
[0.23 0.7 ]
0.7309288996403119
1.1970190380532486
[0.73 1.2 ]
1.52547086688358
1.4618663604676712
[1.53 1.46]
0.7293599071017203
1.32

0.7012640902608378
1.267732703039199
[0.7  1.27]
0.17463744200520104
0.7411060547835622
[0.17 0.74]
-0.19194223229908702
-0.17534313097715803
[-0.19 -0.18]
0.22093137061433057
0.6627941118429918
[0.22 0.66]
0.6959986048360748
1.137861346064736
[0.7  1.14]
1.4587391002561518
1.3921081778714284
[1.46 1.39]
0.7002149388860371
1.2656874843097425
[0.7  1.27]
0.17481624920667416
0.7402887946303796
[0.17 0.74]
-0.19143151151504822
-0.17533060717392646
[-0.19 -0.18]
0.2205513903380644
0.6616541710141932
[0.22 0.66]
0.6948835407020404
1.1359863213781691
[0.69 1.14]
1.4565691749925627
1.3898815328083431
[1.46 1.39]
0.6991621201416554
1.2636470236665254
[0.7  1.26]
0.1749884865406941
0.7394733900655641
[0.17 0.74]
-0.19092617133010947
-0.17531325461144487
[-0.19 -0.18]
0.22017278345238067
0.660518350357142
[0.22 0.66]
0.693771447006638
1.1341170139113994
[0.69 1.13]
1.4544028837718495
1.3876608261664698
[1.45 1.39]
0.6981057703256718
1.2616113072587736
[0.7  1.26]
0.17515428664852684
0.7386598235

...

[0.02 0.05]
0.015077122718966149
0.04988298686510596
[0.02 0.05]
-0.008138348953287647
-0.008155692315528526
[-0.01 -0.01]
0.009450156816696658
0.028350470450089975
[0.01 0.03]
0.03032862177617259
0.04922893540956591
[0.03 0.05]
0.0649168041465574
0.06075832953302751
[0.06 0.06]
0.018163694673304337
0.05296614462081867
[0.02 0.05]
0.015075669279346754
0.049878119226861084
[0.02 0.05]
-0.008137523777914352
-0.00815486341629168
[-0.01 -0.01]
0.009449199587293348
0.028347598761880043
[0.01 0.03]
0.03032555102621693
0.049223950200803626
[0.03 0.05]
0.06491023495950993
0.060752178178567956
[0.06 0.06]
0.018161723119518636
0.05296075953856941
[0.02 0.05]
0.015074216120706085
0.04987325253975686
[0.02 0.05]
-0.008136698769110218
-0.0081540346847839
[-0.01 -0.01]
0.009448242551049885
0.028344727653149656
[0.01 0.03]
0.030322480895670533
0.0492189659977703
[0.03 0.05]
0.0649036670968801
0.060746028064840155
[0.06 0.06]
0.01815975198577001
0.052955375546321806
[0.02 0.05]
0.015072763242962459
0.

[0.06 0.06]
0.018104730238334282
0.05280506496890422
[0.02 0.05]
0.015032196380501933
0.04973253111107187
[0.02 0.05]
-0.008112845746383684
-0.008130074206142174
[-0.01 -0.01]
0.009420572263308103
0.02826171678992431
[0.01 0.03]
0.030233715715543875
0.04907486024216008
[0.03 0.05]
0.0647137734128036
0.06056821280791332
[0.06 0.06]
0.018102771228138748
0.052799712443802514
[0.02 0.05]
0.01503075161347045
0.04972769282913422
[0.02 0.05]
-0.008112025711396131
-0.008129250483032237
[-0.01 -0.01]
0.009419620994866902
0.02825886298460071
[0.01 0.03]
0.030230664080749564
0.04906990607048337
[0.03 0.05]
0.06470724509778289
0.060562099742827814
[0.06 0.06]
0.01810081263402205
0.052794360998867675
[0.02 0.05]
0.015029307124906327
0.04972285548975195
[0.02 0.05]
-0.00811120584143013
-0.008128426926089193
[-0.01 -0.01]
0.009418669917789864
0.028256009753369594
[0.01 0.03]
0.030227613059608437
0.04906495289518817
[0.03 0.05]
0.06470071809487826
0.060555987906944775
[0.06 0.06]
0.01809885445585363
0

0.009391171667978787
0.02817351500393636
[0.01 0.03]
0.030139399558669386
0.04892174289462696
[0.03 0.05]
0.06451200401373194
0.06037927771298114
[0.06 0.06]
0.018042247639197068
0.05263431831722533
[0.02 0.05]
0.01498610155720706
0.04957817223523532
[0.01 0.05]
-0.00808668623191175
-0.008103797237561702
[-0.01 -0.01]
0.009390226305166689
0.028170678915500066
[0.01 0.03]
0.030136366861664904
0.04891681947199828
[0.03 0.05]
0.06450551619166972
0.06037320258199989
[0.06 0.06]
0.018040301878794962
0.05262900019652076
[0.02 0.05]
0.014984665661360419
0.04957336397908622
[0.01 0.05]
-0.008085871453089533
-0.008102978807038662
[-0.01 -0.01]
0.0093892811319452
0.028167843395835602
[0.01 0.03]
0.0301333347726284
0.0489118970365188
[0.03 0.05]
0.0644990296695733
0.060367128668833765
[0.06 0.06]
0.018038356530304694
0.05262368314562233
[0.02 0.05]
0.014983230041421297
0.049568556656738934
[0.01 0.05]
-0.00808505683771002
-0.008102160541089358
[-0.01 -0.01]
0.00938833614825748
0.02816500844477244

[-0.01 -0.01]
0.009362893025356539
0.028088679076069614
[0.01 0.03]
0.030048682376783098
0.04877446842749617
[0.03 0.05]
0.06431793326017904
0.06019755205529482
[0.06 0.06]
0.01798405348525195
0.05247523875947364
[0.02 0.05]
0.01494314437931038
0.04943432965353207
[0.01 0.05]
-0.008062313766549256
-0.008079315711117023
[-0.01 -0.01]
0.009361953325626405
0.028085859976879214
[0.01 0.03]
0.03004566783984596
0.04876957449109877
[0.03 0.05]
0.06431148426831743
0.06019151330058926
[0.06 0.06]
0.017982120026169363
0.05246995259356458
[0.02 0.05]
0.014941716726205562
0.04942954929360078
[0.01 0.05]
-0.008061503869781356
-0.008078502196366515
[-0.01 -0.01]
0.009361013813791319
0.028083041441373954
[0.01 0.03]
0.0300426539054416
0.04876468153302423
[0.03 0.05]
0.06430503656480575
0.06018547575281229
[0.06 0.06]
0.017980186975141213
0.0524646674878682
[0.02 0.05]
0.01494028934663412
0.0494247698593611
[0.01 0.05]
-0.008060694134996146
-0.008077688844714562
[-0.01 -0.01]
0.009360074489795093
0.02

0.06412502237836076
0.06001691296770219
[0.06 0.06]
0.017926226699699843
0.05231711368792537
[0.02 0.05]
0.014900433455414419
0.049291320443639944
[0.01 0.05]
-0.008038087129448479
-0.008054981018517302
[-0.01 -0.01]
0.009333849453124642
0.028001548359373928
[0.01 0.03]
0.029955511102337996
0.048623210008587284
[0.03 0.05]
0.06411861187021883
0.060010910264547565
[0.06 0.06]
0.01792430542692869
0.052311859190665874
[0.02 0.05]
0.014899013974278175
0.04928656773801536
[0.01 0.05]
-0.008037282071143181
-0.00805417237553803
[-0.01 -0.01]
0.009332915552120954
0.02799874665636286
[0.01 0.03]
0.029952515160508713
0.04861834626475062
[0.03 0.05]
0.0641122026389485
0.060004908757563875
[0.06 0.06]
0.017922384558403157
0.05230660574413965
[0.02 0.05]
0.014897594764331099
0.049281815950067594
[0.01 0.05]
-0.008036477173375814
-0.008053363894199687
[-0.01 -0.01]
0.009331981837281313
0.02799594551184394
[0.01 0.03]
0.02994951981566342
0.048613483490226046
[0.03 0.05]
0.06410579468416942
0.05999890

#### Let's plot the results of gradient descent:

In [15]:
fig,ax = plt.subplots(1,1,figsize=(5,4))
# plot the probability 
plt_prob(ax, w_out, b_out)

# Plot the original data
ax.set_ylabel(r'$x_1$')
ax.set_xlabel(r'$x_0$')   
ax.axis([0, 4, 0, 3.5])
plot_data(X_train,y_train,ax)

# Plot the decision boundary
x0 = -b_out/w_out[0]
x1 = -b_out/w_out[1]
ax.plot([0,x0],[x1,0], c=dlc["dlblue"], lw=1)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In the plot above:
 - the shading reflects the probability y=1 (result prior to decision boundary)
 - the decision boundary is the line at which the probability = 0.5
 

## Another Data set
Let's return to a one-variable data set. With just two parameters, $w$, $b$, it is possible to plot the cost function using a contour plot to get a better idea of what gradient descent is up to.

In [16]:
x_train = np.array([0., 1, 2, 3, 4, 5])
y_train = np.array([0,  0, 0, 1, 1, 1])

As before, we'll use a helper function to plot this data. The data points with label $y=1$ are shown as red crosses, while the data points with label $y=0$ are shown as blue circles.

In [17]:
fig,ax = plt.subplots(1,1,figsize=(4,3))
plt_tumor_data(x_train, y_train, ax)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In the plot below, try:
- changing $w$ and $b$ by clicking within the contour plot on the upper right.
    - changes may take a second or two
    - note the changing value of cost on the upper left plot.
    - note the cost is accumulated by a loss on each example (vertical dotted lines)
- run gradient descent by clicking the orange button.
    - note the steadily decreasing cost (contour and cost plot are in log(cost) 
    - clicking in the contour plot will reset the model for a new run
- to reset the plot, rerun the cell

In [18]:
w_range = np.array([-1, 7])
b_range = np.array([1, -14])
quad = plt_quad_logistic( x_train, y_train, w_range, b_range )

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

## Congratulations!
You have:
- examined the formulas and implementation of calculating the gradient for logistic regression
- utilized those routines in
    - exploring a single variable data set
    - exploring a two-variable data set